In [1104]:
import folium
import pandas as pd
from folium import plugins
from folium.plugins import HeatMap

In [1042]:
routes_df = pd.read_csv('../../data/Project Data-20221123/gtfs3Sept/routes.csv')
routes_df.head()

route_id route_short_name            route_long_name  route_type  \
0         2                1  GARE DE L'OUEST - STOCKEL           1   
1         4                2        SIMONIS - ELISABETH           1   
2         5                3      ESPLANADE - CHURCHILL           0   
3        10                4  GARE DU NORD - STALLE (P)           0   
4         1                5  ERASME - HERRMANN-DEBROUX           1   

  route_color route_text_color  
0      C4008F           FFFFFF  
1      F57000           FFFFFF  
2      B5BA05           000000  
3      F25482           000000  
4      E6B012           FFFFFF

In [1100]:
stops_df = pd.read_csv('../../data/Project Data-20221123/gtfs3Sept/stops.csv')
stops_df.head()

stop_id   stop_name   stop_lat  stop_lon  location_type  parent_station
0    0089  MONTGOMERY  50.838006  4.408970            0.0            37.0
1   0470F     SIMONIS  50.863666  4.329612            0.0             0.0
2    0471     SIMONIS  50.863732  4.329236            0.0            53.0
3    0472     SIMONIS  50.863543  4.329023            0.0            53.0
4   0473F     SIMONIS  50.863418  4.330031            0.0             0.0

In [1123]:
stops_heat_df = stops_df
stops_heat_df = stops_heat_df.groupby(['stop_name']).apply(lambda x: x[['stop_lat', 'stop_lon']].values.tolist()).reset_index(name='geom')
for _, ts in stops_heat_df.iterrows():
    lat = sum([i[0] for i in ts['geom']])/len(ts['geom'])
    lon = sum([i[1] for i in ts['geom']])/len(ts['geom'])
    ts['geom'] = (lat, lon)
stops_heat_df.tail()

stop_name                             geom
1124  ZAMAN-FOREST NAT.   (50.814018499999996, 4.324917)
1125           ZAVELPUT  (50.8944815, 4.382611499999999)
1126          ZEECRABBE            (50.804317, 4.354863)
1127      ZENOBE GRAMME           (50.879793, 4.3840135)
1128             ZEPHYR   (50.846961, 4.421212000000001)

In [930]:
trips_df = pd.read_csv('../../data/Project Data-20221123/gtfs3Sept/trips.csv')
trips_df.head()

route_id  service_id             trip_id trip_headsign  direction_id  \
0        24   235954071  112387248235954071       SIMONIS             1   
1        24   235954071  112387249235954071       SIMONIS             1   
2        24   235954071  112387253235954071       SIMONIS             1   
3        24   235954071  112387254235954071       SIMONIS             1   
4        24   235954071  112387255235954071       SIMONIS             1   

   block_id  shape_id  
0   8902800  087b0196  
1   8902802  087b0196  
2   8902801  087b0196  
3   8902800  087b0196  
4   8902802  087b0196

In [931]:
stop_times_df = pd.read_csv('../../data/Project Data-20221123/gtfs3Sept/stop_times.csv')
stop_times_df.head()

trip_id arrival_time departure_time stop_id  stop_sequence  \
0  112387248235954071     21:07:00       21:07:00    4014              1   
1  112387248235954071     21:09:00       21:09:00    3231              2   
2  112387248235954071     21:10:08       21:10:08    3232              3   
3  112387248235954071     21:11:00       21:11:00    3233              4   
4  112387248235954071     21:11:43       21:11:43    3239              5   

   pickup_type  drop_off_type  
0            0              0  
1            0              0  
2            0              0  
3            0              0  
4            0              0

In [932]:
shapes_df = pd.read_csv('../../data/Project Data-20221123/gtfs3Sept/shapes.csv')
shapes_df.head()

shape_id  shape_pt_lat  shape_pt_lon  shape_pt_sequence
0  001m0042     50.841872      4.464541              10001
1  001m0042     50.843270      4.463607              10002
2  001m0042     50.843517      4.463443              10003
3  001m0042     50.843755      4.463283              10004
4  001m0042     50.844054      4.463082              10005

In [1036]:
villo_df = pd.read_csv('../../data/Project Data-20221123/gtfs3Sept/villo.csv')
villo_df = villo_df[['gid', 'name_fr', 'bike_stands', 'geom']]
villo_df = villo_df[villo_df['bike_stands'] >= 30]
villo_df.head()

gid             name_fr  bike_stands  \
1     1    Gare D'Etterbeek           30   
35   35               Trone           32   
43   43     Gare De L'Ouest           30   
57   57  Gare De Luxembourg           44   
58   58        Gare Du Nord           43   

                                            geom  
1    POINT (4.389324995898302 50.82220704190273)  
35    POINT (4.365980995906002 50.8404580418794)  
43   POINT (4.320627995918081 50.84886604186471)  
57    POINT (4.373019995904048 50.8384110418825)  
58  POINT (4.359419995909604 50.859181041857354)

In [1082]:
train_stations_df = stops_df[(stops_df['stop_name'].str.contains('GARE')) | ((stops_df['stop_name'].str.contains('STATION')))]
train_stations_df = train_stations_df.groupby(['stop_name']).apply(lambda x: x[['stop_lat', 'stop_lon']].values.tolist()).reset_index(name='geom')
for _, ts in train_stations_df.iterrows():
    lat = sum([i[0] for i in ts['geom']])/len(ts['geom'])
    lon = sum([i[1] for i in ts['geom']])/len(ts['geom'])
    ts['geom'] = (lat, lon)
train_stations_df.head(32)

stop_name                                     geom
0     BERCHEM STATION          (50.8724244, 4.290135600000001)
1      BOITSFORT GARE                    (50.79551, 4.4074805)
2       BOONDAEL GARE           (50.801303499999996, 4.393229)
3      BORDET STATION           (50.87843690000001, 4.4099269)
4          DEUX GARES                   (50.832105, 4.3249325)
5      ETTERBEEK GARE   (50.82210633333333, 4.388848499999999)
6       GARE CENTRALE  (50.846069357142866, 4.357924785714285)
7        GARE D'EVERE                     (50.867563, 4.40134)
8     GARE DE BERCHEM                  (50.8724244, 4.2901356)
9   GARE DE BOCKSTAEL                  (50.8797965, 4.3477585)
10  GARE DE HAREN-SUD           (50.889784000000006, 4.415755)
11      GARE DE JETTE             (50.88018025000001, 4.33028)
12    GARE DE L'OUEST   (50.84880127272727, 4.321250545454546)
13  GARE DE LINKEBEEK  (50.774116666666664, 4.338733666666666)
14  GARE DE SAINT-JOB         (50.794442499999995, 4.36189025)
15       GARE DU MIDI  (50.83676642857143, 4.3377580714285715)
16       GARE DU NORD  (50.86043633333333, 4.3595894444444445)
17    GARE FOREST-EST          (50.8092165, 4.320593000000001)
18        LOT STATION                    (50.765858, 4.273708)
19     MOENSBERG GARE                    (50.779011, 4.332418)
20    SCHAERBEEK GARE                   (50.877594, 4.3796142)
21        STATION LOT                    (50.767019, 4.274953)
22   TERVUREN STATION                   (50.8297355, 4.513448)
23  VILVOORDE STATION                   (50.924035, 4.4314535)
24     WATERMAEL GARE                   (50.8097245, 4.399329)

In [1131]:
communes_df = pd.read_csv('../../data/Project Data-20221123/gtfs3Sept/communes.csv', sep=';')
communes_df = communes_df[['Geo Shape', 'Nom de la commune', 'Région']]
communes_df = communes_df[communes_df['Région'] == 'Région de Bruxelles-Capitale']

communes_populations_df = pd.DataFrame(
    {
        'Nom de la commune': ['Auderghem', 'Anderlecht', 'Berchem-Sainte-Agathe', 'Bruxelles', 'Etterbeek', 'Evere', 'Forest', 'Ganshoren', 'Ixelles', 'Jette', 'Koekelberg', 'Molenbeek-Saint-Jean', 'Saint-Gilles', 'Saint-Josse-ten-Noode', 'Schaerbeek', 'Uccle', 'Watermael-Boitsfort', 'Woluwe-Saint-Lambert', 'Woluwe-Saint-Pierre'],
        'Population': [120009, 34342, 25195, 183287, 48194, 42444, 56441, 25222, 87385, 52459, 21886, 97365, 49094, 27199, 131548, 83631, 25318, 57583, 42066]
    }
)

communes_df = communes_df.merge(communes_populations_df)
communes_df = communes_df[['Geo Shape', 'Nom de la commune', 'Population']]

communes_df.head(32)

Geo Shape      Nom de la commune  \
0   {"coordinates": [[[4.454655661, 50.818421918],...              Auderghem   
1   {"coordinates": [[[4.454655661, 50.818421918],...    Woluwe-Saint-Pierre   
2   {"coordinates": [[[[4.358339713, 50.830613127]...                Ixelles   
3   {"coordinates": [[[4.306451557, 50.81244218], ...                 Forest   
4   {"coordinates": [[[4.314064149, 50.867229406],...              Ganshoren   
5   {"coordinates": [[[4.407621338, 50.838866602],...   Woluwe-Saint-Lambert   
6   {"coordinates": [[[4.335632738, 50.848145401],...             Anderlecht   
7   {"coordinates": [[[4.340036216, 50.84024011], ...              Bruxelles   
8   {"coordinates": [[[4.30709499, 50.864255333], ...             Koekelberg   
9   {"coordinates": [[[4.404322868, 50.827026305],...              Etterbeek   
10  {"coordinates": [[[4.313768125, 50.893311233],...                  Jette   
11  {"coordinates": [[[4.335632738, 50.848145401],...   Molenbeek-Saint-Jean   
12  {"coordinates": [[[4.388388718, 50.881065052],...                  Evere   
13  {"coordinates": [[[4.398038701, 50.813293061],...    Watermael-Boitsfort   
14  {"coordinates": [[[4.314064149, 50.867229406],...  Berchem-Sainte-Agathe   
15  {"coordinates": [[[4.384083308, 50.851425635],...  Saint-Josse-ten-Noode   
16  {"coordinates": [[[4.35718598, 50.860313255], ...             Schaerbeek   
17  {"coordinates": [[[4.368122588, 50.814862863],...                  Uccle   
18  {"coordinates": [[[[4.35630851, 50.834726162],...           Saint-Gilles   

    Population  
0       120009  
1        42066  
2        87385  
3        56441  
4        25222  
5        57583  
6        34342  
7       183287  
8        21886  
9        48194  
10       52459  
11       97365  
12       42444  
13       25318  
14       25195  
15       27199  
16      131548  
17       83631  
18       49094

# Exceptions:

## 7 VANDERKINDERE - HEYSEL

Because the Churchill roundabout is a tram depot, few trams make a complete trip from terminus to terminus (**VANDERKINDERE** to **HEYSEL** and vice-versa). The vast majority of trams (cfr. below) make a short trip from depot to terminus (**VANDERKINDERE** to **CHURCHILL**) and vice-versa (**CHURCHILL** to **VANDERKINDERE**). After this short trip, the trams then depart within 5-15 minutes, which could explain why a such terminus-to-terminus *trip* could be split into **two trips**.

```python
('VANDERKINDERE', 'CHURCHILL', 'CHURCHILL') 962
('CHURCHILL', 'CHURCHILL', 'CAVELL', 'GOSSART', 'LONGCHAMP', 'BASCULE', 'LEGRAND', 'CAMBRE-ETOILE', 'BUYL', 'ROFFIAEN', 'ETTERBEEK GARE', 'VUB', 'ARSENAL', 'PETILLON', 'BOILEAU', 'MONTGOMERY', 'GEORGES HENRI', 'DIAMANT', 'MEISER', 'LEOPOLD III', 'CHAZAL', 'HELIOTROPES', 'LOUIS BERTRAND', 'HOP. PAUL BRIEN', 'DEMOLDER', 'PRINC. ELISABETH', 'DOCKS BRUXSEL', 'VAN PRAET', 'HEEMBEEK', 'BUISSONNETS', 'ARAUCARIA', 'DE WAND', 'SAINT-LAMBERT', 'HEYSEL') 789
('HEYSEL', 'SAINT-LAMBERT', 'DE WAND', 'ARAUCARIA', 'BUISSONNETS', 'HEEMBEEK', 'VAN PRAET', 'DOCKS BRUXSEL', 'PRINC. ELISABETH', 'DEMOLDER', 'HOP. PAUL BRIEN', 'LOUIS BERTRAND', 'HELIOTROPES', 'CHAZAL', 'LEOPOLD III', 'MEISER', 'DIAMANT', 'GEORGES HENRI', 'MONTGOMERY', 'BOILEAU', 'PETILLON', 'ARSENAL', 'VUB', 'ETTERBEEK GARE', 'ROFFIAEN', 'BUYL', 'CAMBRE-ETOILE', 'LEGRAND', 'BASCULE', 'LONGCHAMP', 'GOSSART', 'CAVELL', 'CHURCHILL', 'CHURCHILL', 'CHURCHILL', 'VANDERKINDERE') 603
('CHURCHILL', 'CHURCHILL', 'VANDERKINDERE') 197
('HEYSEL', 'SAINT-LAMBERT', 'DE WAND', 'ARAUCARIA', 'BUISSONNETS', 'HEEMBEEK', 'VAN PRAET', 'DOCKS BRUXSEL', 'PRINC. ELISABETH', 'DEMOLDER', 'HOP. PAUL BRIEN', 'LOUIS BERTRAND', 'HELIOTROPES', 'CHAZAL', 'LEOPOLD III', 'MEISER', 'DIAMANT', 'GEORGES HENRI', 'MONTGOMERY', 'BOILEAU', 'PETILLON', 'ARSENAL', 'VUB', 'ETTERBEEK GARE', 'ROFFIAEN', 'BUYL', 'CAMBRE-ETOILE', 'LEGRAND', 'BASCULE', 'LONGCHAMP', 'GOSSART', 'CAVELL', 'CHURCHILL', 'CHURCHILL') 191
('BOILEAU', 'MONTGOMERY', 'GEORGES HENRI', 'DIAMANT', 'MEISER', 'LEOPOLD III', 'CHAZAL', 'HELIOTROPES', 'LOUIS BERTRAND', 'HOP. PAUL BRIEN', 'DEMOLDER', 'PRINC. ELISABETH', 'DOCKS BRUXSEL', 'VAN PRAET', 'HEEMBEEK', 'BUISSONNETS', 'ARAUCARIA', 'DE WAND', 'SAINT-LAMBERT', 'HEYSEL') 137
```

## 4 12 GARE DU NORD - STALLE (P)

Some 600 trips start or end at a stop called **PROGRES**.

```python
('GARE DU NORD', 'ROGIER', 'DE BROUCKERE', 'BOURSE', 'ANNEESSENS', 'LEMONNIER', 'GARE DU MIDI', 'PORTE DE HAL', 'PARVIS ST-GILLES', 'HORTA', 'ALBERT', 'BERKENDAEL', 'VANDERKINDERE', 'MESSIDOR', 'BOETENDAEL', 'HEROS', 'GLOBE', 'WAGON', 'EGIDE VAN OPHEM', 'CARREFOUR STALLE', 'STALLE (P)') 969
('STALLE (P)', 'CARREFOUR STALLE', 'EGIDE VAN OPHEM', 'WAGON', 'GLOBE', 'HEROS', 'BOETENDAEL', 'MESSIDOR', 'VANDERKINDERE', 'BERKENDAEL', 'ALBERT', 'HORTA', 'PARVIS ST-GILLES', 'PORTE DE HAL', 'GARE DU MIDI', 'LEMONNIER', 'ANNEESSENS', 'BOURSE', 'DE BROUCKERE', 'ROGIER', 'GARE DU NORD') 911
('PROGRES', 'GARE DU NORD', 'ROGIER', 'DE BROUCKERE', 'BOURSE', 'ANNEESSENS', 'LEMONNIER', 'GARE DU MIDI', 'PORTE DE HAL', 'PARVIS ST-GILLES', 'HORTA', 'ALBERT', 'BERKENDAEL', 'VANDERKINDERE', 'MESSIDOR', 'BOETENDAEL', 'HEROS', 'GLOBE', 'WAGON', 'EGIDE VAN OPHEM', 'CARREFOUR STALLE', 'STALLE (P)') 327
('STALLE (P)', 'CARREFOUR STALLE', 'EGIDE VAN OPHEM', 'WAGON', 'GLOBE', 'HEROS', 'BOETENDAEL', 'MESSIDOR', 'VANDERKINDERE', 'BERKENDAEL', 'ALBERT', 'HORTA', 'PARVIS ST-GILLES', 'PORTE DE HAL', 'GARE DU MIDI', 'LEMONNIER', 'ANNEESSENS', 'BOURSE', 'DE BROUCKERE', 'ROGIER', 'GARE DU NORD', 'PROGRES') 327
('STALLE (P)', 'CARREFOUR STALLE', 'EGIDE VAN OPHEM', 'WAGON', 'GLOBE', 'HEROS', 'BOETENDAEL', 'MESSIDOR', 'VANDERKINDERE') 74
('GARE DU NORD', 'ROGIER', 'DE BROUCKERE', 'BOURSE', 'ANNEESSENS', 'LEMONNIER', 'GARE DU MIDI', 'PORTE DE HAL', 'PARVIS ST-GILLES', 'HORTA', 'ALBERT', 'BERKENDAEL', 'VANDERKINDERE', 'MESSIDOR', 'BOETENDAEL', 'HEROS', 'GLOBE', 'WAGON', 'EGIDE VAN OPHEM', 'CARREFOUR STALLE') 46
('CARREFOUR STALLE', 'EGIDE VAN OPHEM', 'WAGON', 'GLOBE', 'HEROS', 'BOETENDAEL', 'MESSIDOR', 'VANDERKINDERE', 'BERKENDAEL', 'ALBERT', 'HORTA', 'PARVIS ST-GILLES', 'PORTE DE HAL', 'GARE DU MIDI', 'LEMONNIER', 'ANNEESSENS', 'BOURSE', 'DE BROUCKERE', 'ROGIER', 'GARE DU NORD') 37
('PROGRES', 'GARE DU NORD', 'ROGIER', 'DE BROUCKERE', 'BOURSE', 'ANNEESSENS', 'LEMONNIER', 'GARE DU MIDI', 'PORTE DE HAL', 'PARVIS ST-GILLES', 'HORTA', 'ALBERT', 'BERKENDAEL', 'VANDERKINDERE', 'MESSIDOR', 'BOETENDAEL', 'HEROS', 'GLOBE', 'WAGON', 'EGIDE VAN OPHEM', 'CARREFOUR STALLE') 19
```

This is solved by considering 2 stops starting from the beginning and 2 stops starting from the end in evaluating if trips start and end at terminals.

## 12 BRUSSELS AIRPORT - BRUSSELS CITY

The **BRUSSELS CITY** stop does not exist in *stops.csv*. However, a quick look at the STIB app and on the most (cfr. below) shows that the **BRUSSELS CITY** stop is the **TRONE** stop in the middle of Brussels.

```python
('BRUSSELS AIRPORT', 'BOURGET', 'DA VINCI', 'GENEVE', 'MEISER', 'SCHUMAN', 'LUXEMBOURG', 'TRONE', 'TRONE') 635
('TRONE', 'TRONE', 'LUXEMBOURG', 'SCHUMAN', 'MEISER', 'GENEVE', 'DA VINCI', 'BOURGET', 'BRUSSELS AIRPORT') 624
('DA VINCI', 'BOURGET', 'BRUSSELS AIRPORT') 110
('DA VINCI', 'GENEVE', 'MEISER', 'SCHUMAN', 'LUXEMBOURG', 'TRONE', 'TRONE') 59
```

This is solved by hard-coding a change of **BRUSSELS CITY** to **TRONE** in the data.

## 19 GROOT-BIJGAARDEN - DE WAND

The data does not contain the stop **GROOT-BIJGAARDEN**. This is possibly due to the stop being outside Brussels.

```python
('HUNDERENVELD', 'AZUR', 'VEREMAN', 'SCHWEITZER', 'VALIDA', 'GOFFIN', 'COLLEGE S.-COEUR', 'BOSSAERT-BASILIQ.', 'BESME', 'SIMONIS', 'BROUSTIN', 'MIROIR', 'PLACE R. ASTRID', 'LENOIR', 'GARE DE JETTE', 'CIM. DE JETTE', 'GUILL. DE GREEF', 'ERNEST SALU', 'STUYVENBERGH', 'SAINT-LAMBERT', 'DE WAND') 884
('DE WAND', 'SAINT-LAMBERT', 'STUYVENBERGH', 'ERNEST SALU', 'GUILL. DE GREEF', 'CIM. DE JETTE', 'GARE DE JETTE', 'LENOIR', 'PLACE R. ASTRID', 'MIROIR', 'BROUSTIN', 'SIMONIS', 'BESME', 'BOSSAERT-BASILIQ.', 'COLLEGE S.-COEUR', 'GOFFIN', 'VALIDA', 'SCHWEITZER', 'VEREMAN', 'AZUR', 'HUNDERENVELD') 881
('MIROIR', 'BROUSTIN', 'SIMONIS', 'BESME', 'BOSSAERT-BASILIQ.', 'COLLEGE S.-COEUR', 'GOFFIN', 'VALIDA', 'SCHWEITZER', 'VEREMAN', 'AZUR', 'HUNDERENVELD') 147
('HUNDERENVELD', 'AZUR', 'VEREMAN', 'SCHWEITZER', 'VALIDA', 'GOFFIN', 'COLLEGE S.-COEUR', 'BOSSAERT-BASILIQ.', 'BESME', 'SIMONIS', 'BROUSTIN', 'MIROIR') 126
('DE WAND', 'SAINT-LAMBERT', 'STUYVENBERGH', 'ERNEST SALU', 'GUILL. DE GREEF', 'CIM. DE JETTE', 'DEMINEURS', 'WOESTE', 'ODON WARLAND', 'BELGICA') 124
('BELGICA', 'ODON WARLAND', 'WOESTE', 'DEMINEURS', 'CIM. DE JETTE', 'GUILL. DE GREEF', 'ERNEST SALU', 'STUYVENBERGH', 'SAINT-LAMBERT', 'DE WAND') 120
```

This has been fixed by considering the closest stop to **GROOT-BIJGAARDEN** within Brussels: **HUNDERENVELD**.

## 25 BOONDAEL GARE - ROGIER

A negligible number of trips, if any, go from terminus to terminus. In one direction, **ROGIER** to **BOONDAEL GARE** for instance, there are **835** trips from **ROGIER** to **COTEAUX** and **824** trips from **COTEAUX** to **BOONDAEL GARE**. Similarly, in the other direction, there are **822** trips from **BOONDAEL GARE** to **COTEAUX** and **843** trips from **COTEAUX** to **ROGIER**.

```python
('COTEAUX', 'ROBIANO', 'LEFRANCQ', 'LIEDTS', 'THOMAS', 'GARE DU NORD', 'ROGIER') 843
('ROGIER', 'GARE DU NORD', 'THOMAS', 'LIEDTS', 'LEFRANCQ', 'ROBIANO', 'COTEAUX') 835
('COTEAUX', 'BIENFAITEURS', 'PATRIE', 'MEISER', 'MEISER', 'DIAMANT', 'GEORGES HENRI', 'MONTGOMERY', 'BOILEAU', 'PETILLON', 'ARSENAL', 'VUB', 'ETTERBEEK GARE', 'ROFFIAEN', 'BUYL', 'ULB', 'SOLBOSCH', 'MARIE-JOSE', 'BRESIL', 'BOONDAEL GARE') 824
('BOONDAEL GARE', 'BRESIL', 'MARIE-JOSE', 'SOLBOSCH', 'ULB', 'JEANNE', 'BUYL', 'ROFFIAEN', 'ETTERBEEK GARE', 'VUB', 'ARSENAL', 'PETILLON', 'BOILEAU', 'MONTGOMERY', 'GEORGES HENRI', 'DIAMANT', 'MEISER', 'PATRIE', 'BIENFAITEURS', 'COTEAUX') 822
('BOILEAU', 'MONTGOMERY', 'GEORGES HENRI', 'DIAMANT', 'MEISER', 'PATRIE', 'BIENFAITEURS', 'COTEAUX', 'ROBIANO', 'LEFRANCQ', 'LIEDTS') 136
('LIEDTS', 'LIEDTS', 'LEFRANCQ', 'ROBIANO', 'COTEAUX', 'BIENFAITEURS', 'PATRIE', 'MEISER', 'MEISER', 'DIAMANT', 'GEORGES HENRI', 'MONTGOMERY', 'BOILEAU') 135
```

## 62 EUROCONTROL - CIMETIERE DE JETTE

The trips on this line reach the stop **EUROCONTROL** but never reach the stop **CIMETIERE DE JETTE**. The vast majority of trips has, as terminals, **EUROCONTROL** and **BIENFAITEURS**.

```python
('EUROCONTROL', 'BOURGET', 'FUSEE', 'DA VINCI', 'LEKAERTS', 'EVERE SHOPPING', 'PENTATHLON', 'LEOPOLD III', 'MEISER', 'PATRIE', 'BIENFAITEURS') 660
('BIENFAITEURS', 'PATRIE', 'MEISER', 'LEOPOLD III', 'PENTATHLON', 'EVERE SHOPPING', 'LEKAERTS', 'DA VINCI', 'FUSEE', 'BOURGET', 'EUROCONTROL') 648
('BIENFAITEURS', 'PATRIE', 'MEISER', 'LEOPOLD III', 'PENTATHLON', 'EVERE SHOPPING', 'LEKAERTS', 'DA VINCI') 36
('DA VINCI', 'FUSEE', 'BOURGET', 'EUROCONTROL') 35
('DA VINCI', 'LEKAERTS', 'EVERE SHOPPING', 'PENTATHLON', 'LEOPOLD III', 'MEISER') 32
```

This has been fixed by replacing **CIMETIERE DE JETTE** with **BIENFAITEURS**.

## 53 WESTLAND SHOPPING - HOPITAL MILITAIRE

The stop **HOPITAL MILITAIRE** had been abbreviated to **HOP. MILITAIRE**. This was promptly accounted for in the code.

```python
('WESTLAND SHOPPING', 'WESTLAND SHOPPING', 'FRUITS', 'WILLEMYNS', 'PETERBOS', 'PRINCE DE LIEGE', 'MACHTENS', 'CANDRIES', 'LEROY', 'CIM. DE MOLENBEEK', 'BASTOGNE', 'BOSSAERT-BASILIQ.', 'RIETHUISEN', 'SIMPSON', 'MIROIR', 'LEOPOLD I', 'WOESTE', 'LOYAUTE', 'EMILE DELVA', 'BOCKSTAEL', 'GARE DE BOCKSTAEL', 'KAREL BOGAERD', 'ARTISTES', 'SCHOLA EUROPEA', 'SERRES ROYALES', 'DE WAND', 'PAGODES', 'LONG BONNIER', 'VERSAILLES', 'BEYSEGHEM', 'KRUIPWEG', 'ZAVELPUT', 'PETER BENOIT', 'VAL MARIA', 'FERME NOS PILIFS', 'HOP. MILITAIRE') 783
('HOP. MILITAIRE', 'HOP. MILITAIRE', 'FERME NOS PILIFS', 'VAL MARIA', 'PETER BENOIT', 'ZAVELPUT', 'KRUIPWEG', 'BEYSEGHEM', 'VERSAILLES', 'LONG BONNIER', 'PAGODES', 'DE WAND', 'SERRES ROYALES', 'SCHOLA EUROPEA', 'ARTISTES', 'KAREL BOGAERD', 'GARE DE BOCKSTAEL', 'BOCKSTAEL', 'EMILE DELVA', 'LOYAUTE', 'WOESTE', 'LEOPOLD I', 'MIROIR', 'SIMPSON', 'RIETHUISEN', 'BOSSAERT-BASILIQ.', 'BASTOGNE', 'CIM. DE MOLENBEEK', 'LEROY', 'CANDRIES', 'MACHTENS', 'PRINCE DE LIEGE', 'PETERBOS', 'WILLEMYNS', 'FRUITS', 'WESTLAND SHOPPING') 769
('HOP. MILITAIRE', 'HOP. MILITAIRE', 'FERME NOS PILIFS', 'VAL MARIA', 'PETER BENOIT', 'ZAVELPUT', 'KRUIPWEG', 'BEYSEGHEM', 'VERSAILLES', 'LONG BONNIER', 'PAGODES', 'DE WAND', 'ESPLANADE', 'MADELON', 'BRUSSELS EXPO', 'MAGNOLIAS', 'ROI BAUDOUIN', 'STADE', 'HOUBA-BRUGMANN', 'STUYVENBERGH', 'SOBIESKI', 'GARE DE BOCKSTAEL', 'BOCKSTAEL', 'EMILE DELVA', 'LOYAUTE', 'WOESTE', 'LEOPOLD I', 'MIROIR', 'SIMPSON', 'RIETHUISEN', 'BOSSAERT-BASILIQ.', 'BASTOGNE', 'CIM. DE MOLENBEEK', 'LEROY', 'CANDRIES', 'MACHTENS', 'PRINCE DE LIEGE', 'PETERBOS', 'WILLEMYNS', 'FRUITS', 'WESTLAND SHOPPING') 38
('WESTLAND SHOPPING', 'WESTLAND SHOPPING', 'FRUITS', 'WILLEMYNS', 'PETERBOS', 'PRINCE DE LIEGE', 'MACHTENS', 'CANDRIES', 'LEROY', 'CIM. DE MOLENBEEK', 'BASTOGNE', 'BOSSAERT-BASILIQ.', 'RIETHUISEN', 'SIMPSON', 'MIROIR', 'LEOPOLD I', 'WOESTE', 'LOYAUTE', 'EMILE DELVA', 'BOCKSTAEL', 'GARE DE BOCKSTAEL', 'SOBIESKI', 'STUYVENBERGH', 'HOUBA-BRUGMANN', 'STADE', 'ROI BAUDOUIN', 'MAGNOLIAS', 'BRUSSELS EXPO', 'MADELON', 'ESPLANADE', 'DE WAND', 'PAGODES', 'LONG BONNIER', 'VERSAILLES', 'BEYSEGHEM', 'KRUIPWEG', 'ZAVELPUT', 'PETER BENOIT', 'VAL MARIA', 'FERME NOS PILIFS', 'HOP. MILITAIRE') 32
```

## 59 HOPITAL ETTERBEEK-IXELLES - BORDET STATION

The stop **HOPITAL ETTERBEEK-IXELLES** had been abbreviated to **HOP. ETT.-IXELLES**. This was promptly accounted for in the code.

```python
('BORDET STATION', 'VANDENHOVEN', 'SAINT-VINCENT', 'PICARDIE', 'CARLI', 'CHAUMONTEL', 'ANATOLE FRANCE', 'HUART-HAMOIR', 'SCHAERBEEK GARE', 'PRINC. ELISABETH', 'VERBOEKHOVEN', 'EENENS', 'ERNEST LAUDE', 'HERMAN', 'COTEAUX', 'GEEFS', 'BOSSUET', 'HOUWAERT', 'BRAEMT', 'GUTENBERG', 'LIVINGSTONE', 'MAELBEEK', 'PARC LEOPOLD', 'JOURDAN', 'NATATION', 'WERY', 'FLAGEY', 'LEVURE', 'HOP. ETT.-IXELLES') 735
('HOP. ETT.-IXELLES', 'LEVURE', 'FLAGEY', 'WERY', 'NATATION', 'ETANGS', 'JOURDAN', 'FROISSART', 'MAELBEEK', 'LIVINGSTONE', 'GUTENBERG', 'SAINT-JOSSE', 'HOUWAERT', 'GEEFS', 'COTEAUX', 'HERMAN', 'ERNEST LAUDE', 'EENENS', 'VERBOEKHOVEN', 'PRINC. ELISABETH', 'SCHAERBEEK GARE', 'HUART-HAMOIR', 'ANATOLE FRANCE', 'CHAUMONTEL', 'CARLI', 'PICARDIE', 'SAINT-VINCENT', 'VANDENHOVEN', 'BORDET STATION') 347
('HOP. ETT.-IXELLES', 'LEVURE', 'FLAGEY', 'WERY', 'NATATION', 'ETANGS', 'JOURDAN', 'FROISSART', 'MAELBEEK', 'LIVINGSTONE', 'GUTENBERG', 'SAINT-JOSSE', 'STEURS', 'GEEFS', 'COTEAUX', 'AZALEES', 'CROSSING', 'HERMAN', 'ERNEST LAUDE', 'EENENS', 'VERBOEKHOVEN', 'PRINC. ELISABETH', 'SCHAERBEEK GARE', 'HUART-HAMOIR', 'ANATOLE FRANCE', 'CHAUMONTEL', 'CARLI', 'PICARDIE', 'SAINT-VINCENT', 'VANDENHOVEN', 'BORDET STATION') 272
('PRINC. ELISABETH', 'SCHAERBEEK GARE', 'HUART-HAMOIR', 'ANATOLE FRANCE', 'CHAUMONTEL', 'CARLI', 'PICARDIE', 'SAINT-VINCENT', 'VANDENHOVEN', 'BORDET STATION') 86
('HOP. ETT.-IXELLES', 'LEVURE', 'FLAGEY', 'WERY', 'NATATION', 'JOURDAN', 'PARC LEOPOLD', 'MAELBEEK', 'LIVINGSTONE', 'GUTENBERG', 'SAINT-JOSSE', 'STEURS', 'GEEFS', 'COTEAUX', 'AZALEES', 'CROSSING', 'HERMAN', 'ERNEST LAUDE', 'EENENS', 'VERBOEKHOVEN', 'PRINC. ELISABETH', 'SCHAERBEEK GARE', 'HUART-HAMOIR', 'ANATOLE FRANCE', 'CHAUMONTEL', 'CARLI', 'PICARDIE', 'SAINT-VINCENT', 'VANDENHOVEN', 'BORDET STATION') 82
```

## 63 GARE CENTRALE - CIMETIERE DE BRUXELLES

The stop **CIMETIERE DE BRUXELLES** had been abbreviated to **CIM. DE BRUXELLES**. This was promptly accounted for in the code.

```python
('CIM. DE BRUXELLES', 'ARBRE UNIQUE', 'OPTIMISME', 'PAUL LEDUC', 'FRANS COURTENS', 'LEOPOLD III', 'MEISER', 'PLASKY', 'JAMBLINNE DE MEUX', 'GUEUX', 'MARGUERITE', 'AMBIORIX', 'WATERLOO WILSON', 'GUTENBERG', 'SAINT-JOSSE', 'MADOU', 'PRESSE', 'TREURENBERG', 'ROSA PARKS', 'GARE CENTRALE') 706
('GARE CENTRALE', 'ROSA PARKS', 'TREURENBERG', 'PRESSE', 'MADOU', 'SAINT-JOSSE', 'GUTENBERG', 'AMBIORIX', 'MICHEL-ANGE', 'GUEUX', 'JAMBLINNE DE MEUX', 'PLASKY', 'MAX-PLASKY', 'MEISER', 'LEOPOLD III', 'FRANS COURTENS', 'PAUL LEDUC', 'OPTIMISME', 'ARBRE UNIQUE', 'CIM. DE BRUXELLES', 'DIABLOTINS', 'CIM. DE BRUXELLES') 640
('GARE CENTRALE', 'ROSA PARKS', 'TREURENBERG', 'PRESSE', 'MADOU', 'SAINT-JOSSE', 'GUTENBERG', 'AMBIORIX', 'MICHEL-ANGE', 'GUEUX', 'JAMBLINNE DE MEUX', 'PLASKY', 'MAX-PLASKY', 'MEISER') 54
('GARE CENTRALE', 'ROSA PARKS', 'TREURENBERG', 'PRESSE', 'MADOU', 'SAINT-JOSSE', 'GUTENBERG', 'AMBIORIX', 'MICHEL-ANGE', 'GUEUX', 'JAMBLINNE DE MEUX', 'PLASKY', 'MAX-PLASKY', 'MEISER', 'LEOPOLD III', 'FRANS COURTENS', 'PAUL LEDUC', 'OPTIMISME', 'ARBRE UNIQUE', 'CIM. DE BRUXELLES') 54
```

## 66 DE BROUCKERE - PEAGE

This may be outdated. As evidenced by the new line name **(66 GARE CENTRALE - PEAGE)** and the data itself, the true terminals are **GARE CENTRALE** and **PEAGE**. This has been accounted for in the code.

```python
('PEAGE', 'CIM. DE BRUXELLES', 'ARTEMIS', 'PADUWA', 'GUILLAUME', 'DUNANT', 'EVERE SHOPPING', 'CONSCIENCE', 'KURTH', 'TERDELT', 'LATINIS', 'LOUIS BERTRAND', 'CROSSING', 'VOLTAIRE', 'POGGE', 'LEHON', 'SAINTE-MARIE', 'SAINTE-MARIE', 'GILLON', 'BOTANIQUE', 'CONGRES', 'ROSA PARKS', 'GARE CENTRALE') 593
('GARE CENTRALE', 'ROSA PARKS', 'TREURENBERG', 'PRESSE', 'MADOU', 'QUETELET', 'BOTANIQUE', 'GILLON', 'SAINTE-MARIE', 'SAINTE-MARIE', 'LEHON', 'POGGE', 'VOLTAIRE', 'CROSSING', 'LOUIS BERTRAND', 'LATINIS', 'TERDELT', 'KURTH', 'CONSCIENCE', "GARE D'EVERE", 'EVERE SHOPPING', 'DUNANT', 'GUILLAUME', 'PADUWA', 'ARTEMIS', 'CIM. DE BRUXELLES', 'DIABLOTINS', 'VILLON', 'PEAGE') 584
('PEAGE', 'CIM. DE BRUXELLES', 'ARTEMIS', 'PADUWA', 'GUILLAUME', 'DUNANT', 'EVERE SHOPPING', 'CONSCIENCE', 'KURTH', 'TERDELT', 'LATINIS', 'LOUIS BERTRAND', 'CROSSING', 'AZALEES', 'COTEAUX', 'COTEAUX', 'ROBIANO', 'MERIDIEN', 'RUE TRAVERSIERE', 'QUETELET', 'MADOU', 'PRESSE', 'TREURENBERG', 'ROSA PARKS', 'GARE CENTRALE') 255
('GARE CENTRALE', 'ROSA PARKS', 'TREURENBERG', 'PRESSE', 'MADOU', 'QUETELET', 'RUE TRAVERSIERE', 'MERIDIEN', 'ROBIANO', 'COTEAUX', 'COTEAUX', 'AZALEES', 'CROSSING', 'LOUIS BERTRAND', 'LATINIS', 'TERDELT', 'KURTH', 'CONSCIENCE', "GARE D'EVERE", 'EVERE SHOPPING', 'DUNANT', 'GUILLAUME', 'PADUWA', 'ARTEMIS', 'CIM. DE BRUXELLES', 'DIABLOTINS', 'VILLON', 'PEAGE') 252
('GARE CENTRALE', 'ROSA PARKS', 'TREURENBERG', 'PRESSE', 'MADOU', 'QUETELET', 'BOTANIQUE', 'GILLON', 'SAINTE-MARIE', 'SAINTE-MARIE', 'LEHON', 'POGGE', 'VOLTAIRE', 'CROSSING', 'LOUIS BERTRAND', 'LATINIS', 'TERDELT', 'KURTH', 'CONSCIENCE', "GARE D'EVERE") 30
('PEAGE', 'CIM. DE BRUXELLES', 'ARTEMIS', 'PADUWA', 'GUILLAUME', 'DUNANT', 'EVERE SHOPPING', 'CONSCIENCE', 'KURTH', 'TERDELT', 'HOP. PAUL BRIEN', 'POGGE', 'LEHON', 'SAINTE-MARIE', 'SAINTE-MARIE', 'GILLON', 'BOTANIQUE', 'CONGRES', 'ROSA PARKS', 'GARE CENTRALE') 21
('CONSCIENCE', 'KURTH', 'TERDELT', 'LATINIS', 'LOUIS BERTRAND', 'CROSSING', 'VOLTAIRE', 'POGGE', 'LEHON', 'SAINTE-MARIE', 'SAINTE-MARIE', 'GILLON', 'BOTANIQUE', 'CONGRES', 'ROSA PARKS', 'GARE CENTRALE') 17
```

## 73 CERIA - GARE DU MIDI

Not yet in the data.

## 74 CLEMENCE EVERARD - UCCLE STALLE

The stop **UCCLE STALLE** had been renamed to  to **UCCLE-STALLE**. This was promptly accounted for in the code.

```python
('UCCLE-STALLE', 'VICTOR ALLARD', 'DECROLY', 'FORESTOISE', 'FOREST NATIONAL', 'GARE FOREST-EST', 'SAINT-DENIS', 'FOREST CENTRE', 'BERVOETS', 'CHARROI', 'ILE SAINTE-HELENE', 'DIGUE DU CANAL', 'VAN KALKEN', 'ARISTIDE BRIAND', 'VEEWEYDE', 'DEBUSSY', 'FRANS HALS', 'MARTIN LUTH. KING', 'MARIE CURIE', 'TREFLES', 'EDDY MERCKX', 'MEYLEMEERSCH', 'ERASME', 'CLEMENCE EVERARD', 'CLEMENCE EVERARD') 492
('CLEMENCE EVERARD', 'ERASME', 'MEYLEMEERSCH', 'EDDY MERCKX', 'TREFLES', 'MARIE CURIE', 'MARTIN LUTH. KING', 'FRANS HALS', 'DEBUSSY', 'VEEWEYDE', 'ARISTIDE BRIAND', 'VAN KALKEN', 'DIGUE DU CANAL', 'ILE SAINTE-HELENE', 'CHARROI', 'BERVOETS', 'FOREST CENTRE', 'SAINT-DENIS', 'GARE FOREST-EST', 'FOREST NATIONAL', 'FORESTOISE', 'DECROLY', 'AULNE', 'VICTOR ALLARD', 'UCCLE-STALLE') 480
('CLEMENCE EVERARD', 'ERASME', 'MEYLEMEERSCH', 'EDDY MERCKX', 'TREFLES', 'MARIE CURIE', 'MARTIN LUTH. KING', 'FRANS HALS', 'DEBUSSY', 'VEEWEYDE', 'ARISTIDE BRIAND', 'VAN KALKEN', 'DIGUE DU CANAL') 31
('DIGUE DU CANAL', 'ILE SAINTE-HELENE', 'CHARROI', 'BERVOETS', 'FOREST CENTRE', 'SAINT-DENIS', 'GARE FOREST-EST', 'FOREST NATIONAL', 'FORESTOISE', 'DECROLY', 'AULNE', 'VICTOR ALLARD', 'UCCLE-STALLE') 30
```

## 90 JACQUES BREL - PETERBOS

Not yet in the data.

In [933]:
def common_trips_on_route(route_short_name):
    
    # print(route_short_name)
    line_df = routes_df[routes_df['route_short_name'] == str(route_short_name)]  # route_id determined from vehicle number
    # print(route_short_name, line_df.iloc[0,2])

    trips_on_line_df = line_df.merge(trips_df)
    trips_on_line_df = trips_on_line_df[['trip_id']]

    stop_times_on_line_df = trips_on_line_df.merge(stop_times_df)
    stop_times_on_line_df = stop_times_on_line_df[['trip_id', 'stop_id', 'stop_sequence']]
    stop_times_on_line_df = stop_times_on_line_df.merge(stops_df, how='left')
    stop_times_on_line_df = stop_times_on_line_df[['trip_id', 'stop_name']]

    stops_per_trip_on_line_df = stop_times_on_line_df.groupby(['trip_id'])['stop_name'].apply(lambda x: tuple(x.tolist())).reset_index(name='stop_sequence')

    trips_per_sequence_df = stops_per_trip_on_line_df.groupby(['stop_sequence'])['trip_id'].count().reset_index(name='count')
    trips_per_sequence_df = trips_per_sequence_df.sort_values(by=['count'], ascending=False)

    top_sequences = [trips_per_sequence_df.iloc[i]['stop_sequence'] for i in range(trips_per_sequence_df.shape[0])]
    top_occurrences = [trips_per_sequence_df.iloc[i]['count'] for i in range(trips_per_sequence_df.shape[0])]

    return pd.DataFrame({'sequences': top_sequences, 'occurrences': top_occurrences})

In [966]:
def find_stops_from_route(route_short_name):

    # print(route_short_name)

    line_df = routes_df[routes_df['route_short_name'] == str(route_short_name)]  # route_id determined from vehicle number
    # print(route_short_name, line_df.iloc[0,2])

    terminals = pd.DataFrame({'stop_name': line_df.iloc[0,2].split(' - ')})

    terminals = terminals.replace('BRUSSELS CITY', 'TRONE')  # 12 BRUSSELS CITY doens't exist, it's the stop TRONE
    terminals = terminals.replace('GROOT-BIJGAARDEN', 'HUNDERENVELD')  # GROOT-BIJGAARDEN isn't in the data, HUNDERENVELD is the closest stop
    terminals = terminals.replace('CIMETIERE DE JETTE', 'BIENFAITEURS')  # CIMETIERE DE JETTE isn't in the data, BIENFAITEURS is the most suitable replacement
    terminals = terminals.replace('HOPITAL MILITAIRE', 'HOP. MILITAIRE')  # Abbreviation
    terminals = terminals.replace('HOPITAL ETTERBEEK-IXELLES', 'HOP. ETT.-IXELLES')  # Abbreviation
    terminals = terminals.replace('CIMETIERE DE BRUXELLES', 'CIM. DE BRUXELLES')  # Abbreviation
    terminals = terminals.replace('UCCLE STALLE', 'UCCLE-STALLE')  # Abbreviation
    if route_short_name == 66:
        terminals = terminals.replace('DE BROUCKERE', 'GARE CENTRALE')  # Outdated data

    terminals = terminals.merge(stops_df).groupby(['stop_name'])['stop_id'].apply(lambda x: tuple(x.tolist())).reset_index(name='stop_ids')
    # print(terminals)
    terminal1_ids, terminal2_ids = terminals['stop_ids'].tolist()  # terminals are now determined from route_id

    # left to fix: 7, 25

    trips_on_line_df = line_df.merge(trips_df)
    # line_trips_df = line_trips_df[line_trips_df['trip_headsign'].isin(terminals)]  # somehow faulty and removes a lot of data
    trips_on_line_df = trips_on_line_df[['trip_id']]

    stop_times_on_line_df = trips_on_line_df.merge(stop_times_df)
    stop_times_on_line_df = stop_times_on_line_df[['trip_id', 'stop_id', 'stop_sequence']]
    stop_times_on_line_df = stop_times_on_line_df.merge(stops_df, how='left')
    stop_times_on_line_df = stop_times_on_line_df[['trip_id', 'stop_id']]

    stops_per_trip_on_line_df = stop_times_on_line_df.groupby(['trip_id'])['stop_id'].apply(lambda x: tuple(x.tolist())).reset_index(name='stop_sequence')

    trips_per_sequence_df = stops_per_trip_on_line_df.groupby(['stop_sequence'])['trip_id'].count().reset_index(name='count')
    trips_per_sequence_df = trips_per_sequence_df.sort_values(by=['count'], ascending=False)

    top_sequences = [trips_per_sequence_df.iloc[i]['stop_sequence'] for i in range(trips_per_sequence_df.shape[0])]

    # for i in range(trips_per_sequence_df.shape[0]):
    #     print(trips_per_sequence_df.iloc[i]['stop_sequence'], trips_per_sequence_df.iloc[i]['count'])

    def is_direct_sequence(seq):
        starts_terminal1 = len([i for i in seq[:2] if i in terminal1_ids]) > 0
        ends_terminal2 = len([i for i in seq[-2:] if i in terminal2_ids]) > 0
        return starts_terminal1 and ends_terminal2

    def is_reverse_sequence(seq):
        starts_terminal2 = len([i for i in seq[:2] if i in terminal2_ids]) > 0
        ends_terminal1 = len([i for i in seq[-2:] if i in terminal1_ids]) > 0
        return starts_terminal2 and ends_terminal1

    for s in top_sequences:
        if is_direct_sequence(s):
            direct_seq = s
        elif is_reverse_sequence(s):
            reverse_seq = s

    # total_count, complete_trip_count, incomplete_trip_count = 0, 0, 0

    # for row in trips_per_sequence_df.iterrows():
    #     count = row[1]['count']
    #     extremities = list(row[1]['stop_sequence'])[:2] + list(row[1]['stop_sequence'])[-2:]
        
    #     total_count += count
    #     if len([elem for elem in extremities if elem in terminals]) == 2:
    #         complete_trip_count += count
    #     else:
    #         incomplete_trip_count += count
        
    # print(total_count, complete_trip_count, incomplete_trip_count)

    # return terminals
    return direct_seq, reverse_seq

def get_route_display_info(route_short_name):
    line_df = routes_df[routes_df['route_short_name'] == str(route_short_name)].iloc[0]
    line_dict = line_df.to_dict()

    route_code = ['train', 'subway', '', 'bus']

    line_dict['route_icon'] = route_code[int(line_dict['route_type'])]
    line_dict['route_color'] = '#' + str(line_dict['route_color'])
    # line_dict['route_text_color'] = 'black' if line_dict['route_text_color'] == '000000' else 'white'
    line_dict['route_text_color'] = 'black'

    return line_dict

In [967]:
def find_shape_from_route(route_short_name):

    # print(route_short_name)

    line_df = routes_df[routes_df['route_short_name'] == str(route_short_name)]  # route_id determined from vehicle number
    # print(route_short_name, line_df.iloc[0,2])

    terminals = pd.DataFrame({'stop_name': line_df.iloc[0,2].split(' - ')})

    terminals = terminals.replace('BRUSSELS CITY', 'TRONE')  # 12 BRUSSELS CITY doens't exist, it's the stop TRONE
    terminals = terminals.replace('GROOT-BIJGAARDEN', 'HUNDERENVELD')  # GROOT-BIJGAARDEN isn't in the data, HUNDERENVELD is the closest stop
    terminals = terminals.replace('CIMETIERE DE JETTE', 'BIENFAITEURS')  # CIMETIERE DE JETTE isn't in the data, BIENFAITEURS is the most suitable replacement
    terminals = terminals.replace('HOPITAL MILITAIRE', 'HOP. MILITAIRE')  # Abbreviation
    terminals = terminals.replace('HOPITAL ETTERBEEK-IXELLES', 'HOP. ETT.-IXELLES')  # Abbreviation
    terminals = terminals.replace('CIMETIERE DE BRUXELLES', 'CIM. DE BRUXELLES')  # Abbreviation
    terminals = terminals.replace('UCCLE STALLE', 'UCCLE-STALLE')  # Abbreviation
    if route_short_name == 66:
        terminals = terminals.replace('DE BROUCKERE', 'GARE CENTRALE')  # Outdated data

    terminals = terminals.merge(stops_df).groupby(['stop_name'])['stop_id'].apply(lambda x: tuple(x.tolist())).reset_index(name='stop_ids')
    terminal1_ids, terminal2_ids = terminals['stop_ids'].tolist()  # terminals are now determined from route_id

    trips_on_line_df = line_df.merge(trips_df)
    trips_on_line_df = trips_on_line_df[['trip_id', 'shape_id']]

    stop_times_on_line_df = trips_on_line_df.merge(stop_times_df)
    stop_times_on_line_df = stop_times_on_line_df[['trip_id', 'stop_id', 'stop_sequence', 'shape_id']]
    stop_times_on_line_df = stop_times_on_line_df.merge(stops_df, how='left')
    stop_times_on_line_df = stop_times_on_line_df[['stop_id', 'trip_id']]

    stops_per_trip_on_line_df = stop_times_on_line_df.groupby(['trip_id'])['stop_id'].apply(lambda x: tuple(x.tolist())).reset_index(name='stop_sequence')

    trips_per_sequence_df = stops_per_trip_on_line_df.groupby(['stop_sequence'])['trip_id'].count().reset_index(name='count')
    trips_per_sequence_df = trips_per_sequence_df.sort_values(by=['count'], ascending=False)

    top_sequences = [trips_per_sequence_df.iloc[i]['stop_sequence'] for i in range(trips_per_sequence_df.shape[0])]

    # for i in range(trips_per_sequence_df.shape[0]):
    #     print(trips_per_sequence_df.iloc[i]['stop_sequence'], trips_per_sequence_df.iloc[i]['count'])

    def is_direct_sequence(seq):
        starts_terminal1 = len([i for i in seq[:2] if i in terminal1_ids]) > 0
        ends_terminal2 = len([i for i in seq[-2:] if i in terminal2_ids]) > 0
        return starts_terminal1 and ends_terminal2

    def is_reverse_sequence(seq):
        starts_terminal2 = len([i for i in seq[:2] if i in terminal2_ids]) > 0
        ends_terminal1 = len([i for i in seq[-2:] if i in terminal1_ids]) > 0
        return starts_terminal2 and ends_terminal1

    for s in top_sequences:
        if is_direct_sequence(s):
            direct_seq = s
        elif is_reverse_sequence(s):
            reverse_seq = s
        
    line_routes_df = pd.DataFrame({'stop_sequence': [direct_seq, reverse_seq]})
    line_routes_df = pd.DataFrame({'shape_id': line_routes_df.merge(stops_per_trip_on_line_df).merge(trips_on_line_df)['shape_id'].unique()[:2]})

    polyline_coordinates_df = line_routes_df.merge(shapes_df)
    polyline_coordinates_df['shape_pt'] = polyline_coordinates_df[['shape_pt_lat', 'shape_pt_lon']].values.tolist()
    polyline_coordinates_df = polyline_coordinates_df.groupby(['shape_id'])['shape_pt'].apply(lambda x: x.tolist()).reset_index(name='coordinates')
    
    polyline_coordinates = [polyline_coordinates_df.iloc[i]['coordinates'] for i in range(polyline_coordinates_df.shape[0])]

    return polyline_coordinates

In [1144]:
def map_stops_from_line(route_numbers:list, direct:int=0):

    stop_sequences = []
    shape_sequences = []
    route_names = []
    locations_df_list = []
    route_display_info = []

    for r_n in route_numbers:
        print(r_n)

        stop_seq = find_stops_from_route(r_n)
        stop_sequences.append(stop_seq)

        shape_seq = find_shape_from_route(r_n)
        shape_sequences.append(shape_seq)

        route_name = get_route_display_info(r_n)['route_short_name'] + ' ' + get_route_display_info(r_n)['route_long_name']
        route_names.append(route_name)

        sequence_df = pd.DataFrame({'stop_id': stop_seq[direct]})
        locations_df = sequence_df.merge(stops_df)
        locations_df_list.append(locations_df)

        route_dict = get_route_display_info(r_n)
        
        route_display_info.append(route_dict)

    stib_map = folium.Map(
        location=[50.8476, 4.3572],
        zoom_start=12,
        # tiles = 'MapBox Bright'
        # tiles = 'Stamen Terrain'
        # tiles = 'Stamen Toner'
        tiles='cartodbdark_matter'
        # tiles='cartodbpositron'
    )

    villos_layer = folium.FeatureGroup(
        name='Villos',
        show=False
    )

    for _, row in villo_df.iterrows():
        fr_name = row['name_fr']
        bike_stands = row['bike_stands']
        location = row['geom'].split('POINT ')[1]
        location = [float(i) for i in location[1:-1].split(' ')]
        location = (location[1], location[0])
        villos_layer.add_child(folium.Marker(
            location=location, # (50.8476, 4.3572)
            popup=('Villo station' + fr_name + '\nNumber of bike stands: ' + str(bike_stands)),
            tooltip=fr_name,
            icon=folium.Icon(
                icon='bicycle',
                prefix='fa',
                icon_color='yellow',
                color='gray'
            )
        ))
    
    train_stations_layer = folium.FeatureGroup(
        name='Train Stations',
        show=False
    )

    for _, row in train_stations_df.iterrows():
        name = row['stop_name']
        location = row['geom']
        train_stations_layer.add_child(
            folium.Marker(
                location=location,
                popup=('Train Station:' + name),
                tooltip=name,
                icon=folium.Icon(
                    icon='train',
                    prefix='fa',
                    icon_color='white',
                    color='gray'
                )
            )
        )

    for i in range(len(stop_sequences)):
        print(i)
        s_markers = folium.FeatureGroup(
            name=route_names[i],
            show=True if route_names[i] in [
                '1 GARE DE L\'OUEST - STOCKEL',
                '5 ERASME - HERRMANN-DEBROUX',
                '8 LOUISE - ROODEBEEK',
                '92 SCHAERBEEK GARE - FORT-JACO'
            ] else False
        )
        for _, stop in locations_df_list[i].iterrows():
            s_markers.add_child(folium.Marker(
                location=[stop['stop_lat'], stop['stop_lon']],
                popup=stop['stop_name'],
                tooltip=stop['stop_name'],
                icon=folium.Icon(
                    icon=route_display_info[i]['route_icon'], 
                    prefix='fa',
                    icon_color=route_display_info[i]['route_color'],
                    color=route_display_info[i]['route_text_color']
                )
            ))
        s_polyline = folium.PolyLine(
            locations=shape_sequences[i],
            color=route_display_info[i]['route_color'],
            weight=4
        )
        s_markers.add_child(s_polyline)
        stib_map.add_child(s_markers)

    stib_map.add_child(villos_layer)
    stib_map.add_child(train_stations_layer)

    heat_data = [row['geom'] for _, row in stops_heat_df.iterrows()]
    HeatMap(
        data=heat_data,
        name='STIB Station Heatmap',
        radius=12,
        show=False
    ).add_to(stib_map)

    # folium.Choropleth(

    # )

    stib_map.add_child(folium.LayerControl())
    
    return stib_map

metros = [1, 2, 5, 6]
trams = [4, 8, 9, 19, 39, 44, 51, 55, 62, 81, 82, 92, 93, 97]
interruped_trams = [3, 7, 25]
buses = [12, 13, 14, 17, 20, 21, 27, 28, 29, 33, 34, 36, 37, 38, 41, 42, 43, 45, 46, 47, 48, 49, 50, 52, 53, 54, 56, 58, 59, 60, 61, 63, 64, 65, 66, 71, 72, 74, 75, 79, 80, 83, 86, 87, 88, 89, 95]
unavailable_buses = [73, 90]
vehicles = metros + trams + buses
available_vehicles = metros + trams + buses

# trial_number = [1, 2, 5, 6, 8, 92]
trial_number = sorted(vehicles)
map_stops_from_line(trial_number)
# for _, row in common_trips_on_route(trial_number).iterrows():
#     print(row['sequences'], row['occurrences'])

1
2
4
5
6
8
9
12
13
14
17
19
20
21
27
28
29
33
34
36
37
38
39
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
58
59
60
61
62
63
64
65
66
71
72
74
75
79
80
81
82
83
86
87
88
89
92
93
95
97
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
